# Terminological enrichment
The goal of terminological enrichment is to associate a set of known terms with new terms that are semantically similar. This can be used for expanding the queries.

## The IR system with relevance feedback

In [1]:
import pandas as pd
import numpy as np
from tqdm.notebook import tqdm

In [2]:
import pymongo
from twitter import TwitterDataset, ENTITY, DOMAIN
from nltk.tokenize import TweetTokenizer
from nltk.corpus import stopwords
from string import punctuation

In [3]:
db = pymongo.MongoClient()['twitter']['tweets']
tdata = TwitterDataset(db)

In [4]:
estats = tdata.entity_queries_stats
dstats = tdata.domain_queries_stats

In [6]:
dstats.head(20)

tweet                           query
domain                                       
47      10721                           Brand
10       6368                          Person
65       5525  Interests and Hobbies Vertical
123      3980              Ongoing News Story
45       3331                  Brand Vertical
35       2961                      Politician
66       2681  Interests and Hobbies Category
67       2573           Interests and Hobbies
3        2042                        TV Shows
46       1988                  Brand Category
30       1015       Entities [Entity Service]
119       827                         Holiday
11        655                           Sport
60        648                         Athlete
56        615                           Actor
88        573                  Political Body
26        566                   Sports League
58        493       Entertainment Personality
6         473                    Sports Event
12        460                     Sports Team

In [7]:
stopw = set(stopwords.words('english'))
tokenizer = TweetTokenizer()
tokenize = lambda text: [word for word in tokenizer.tokenize(text.lower()) 
                         if word not in punctuation and word not in stopw and not word.startswith('http')] 

### Naive search engine

In [8]:
from search import TfIdfSearchEngine

In [9]:
E = TfIdfSearchEngine(tdata.search_base, tokenize)

In [15]:
query = 'COVID-19'
ground_truth = tdata.ground_truth(query, query_type=ENTITY)
ranking = E.search('war battle fight armed')

In [16]:
tp, fp, fn, tn = TfIdfSearchEngine.feedback(ranking, 
                                            ground_truth, top_k=4500)

In [17]:
print(len(tp), len(fp), len(fn), len(tn))
print('precision', len(tp) / (len(tp) + len(fp)))
print('recall', len(tp) / (len(tp) + len(fn)))

807 3693 3173 14677
precision 0.17933333333333334
recall 0.2027638190954774


In [18]:
T = dict([(x, y) for x, y in tdata.search_base])
for a, b, c in ranking:
    print(a, b, c)
    print(T[b])
    print()

3133 1474090847750795273 0.2645367229298511
'They keep telling us: war, war, war': Putin accuses west of expanding towards Russia – video https://t.co/Fa4evFwsrF

14749 1473223466379665409 0.26007723181647735
US intelligence secretly plans to train Ukraine army to fight war against Russia
https://t.co/AuIgZbdJ14 https://t.co/c33EvKTqxC

19734 1473232778225410050 0.26007723181647735
US intelligence secretly plans to train Ukraine army to fight war against Russia
https://t.co/AuIgZaW89w https://t.co/0Km1hYIimM

15437 1465600125955461124 0.24178565309583333
It is the linguistic equivalent of the Battle of Troy. 

And the reason for the fight? How to pronounce the name of the new coronavirus variant

 https://t.co/TQ8EizDcKi

4743 1485917735615930374 0.2390161658281661
Brave Isla Caton, 7, dies after inspirational rare cancer fight after 5-year battle https://t.co/3Etts5DBxF https://t.co/OtvQzrswdI

5389 1485927677789880320 0.2390161658281661
Brave Isla Caton, 7, dies after inspirational r

9197 1497892609947226113 0.07438413565254184
🔴 Liz Truss has backed Britons going to Ukraine to join the fight against the Russian invasion.

Ms Truss said she feared Mr Putin could deploy “even worse” “most unsavoury weapons” as he faces tougher than expected resistance

https://t.co/eLB3C77it7

3665 1498980063936712704 0.07393042270673063
Thousands of Russian scientists risk JAIL as they slam Putin's 'senseless' invasion of Ukraine

+ 6,100 scientists have told Putin 'there is no rational justification for this war' 

Read More: https://t.co/XbuogGFGbp https://t.co/zepBTEe5Oo

12542 1490754750882660352 0.0737851529161452
Emmanuel Macron has started talks with Vladimir Putin in Moscow in an effort to 'de-escalate' the crisis in Ukraine and prevent an all-out war in eastern Europe. Here's what the French president is aiming to discuss: https://t.co/GwwkadTGHB

11309 1472824204701671427 0.07372465959420785
The Duchess of Cornwall’s father produced a makeshift news bulletin for his fello

269 1468138708708773888 0.0
Liberal senator Gerard Rennick’s vaccine claims condemned by health officials in Covid inquiry https://t.co/VydDjkMQjo

270 1470710353482993665 0.0
Why are boosters much better at protecting against Omicron than two doses?

A third dose boosts the immune system so significantly that it creates a much better army of antibodies to swarm the virus — even if it has mutated considerably https://t.co/ih72zs4PHG https://t.co/rryNMHtCvZ

271 1463653456082870275 0.0
From environment to economy: what to expect from new German government https://t.co/NZyrlvlxcO

272 1496573453511626755 0.0
Queen holds regular weekly telephone audience with Boris Johnson despite battling Covid https://t.co/CWTdDOpzsk

273 1467867151872802819 0.0
Boris Johnson orders de-escalation of tensions with France https://t.co/aPiBtsGtkU

274 1488279809461559296 0.0
Masks on flights will be one of the last coronavirus restrictions to be dropped globally and could remain policy for years, experts h


611 1466825821880995843 0.0
‘Heartbreaking’ clean-up of animal corpses as Canada floodwaters ebb https://t.co/gECWn2sde9

612 1471061517810475011 0.0
Fire traps hundreds of people at Hong Kong World Trade Centre – video https://t.co/UlvtOO8I3Z

613 1469255822609813504 0.0
Steakhouse hits back at one-star TripAdvisor review saying it will stay 'naff'

https://t.co/pUPzfWg47H https://t.co/tLCo9uKVbU

614 1472635932700463117 0.0
🔴 Hong Kong Chief Executive Carrie Lam is facing criticism over the new electoral model https://t.co/ePsx7VG96a

615 1484100566934503424 0.0
"So far my unwavering reply has been a pretty instant no, and I would still have to be convinced that an existing place which had been going downhill could be resurrected" | Writes Mark Hix  https://t.co/Hae4igwwwt

616 1468189798707826689 0.0
Vanilla Wafer Cookies https://t.co/JCZoWzUUPU #oldfashionedrecipes #recipe

617 1475432220244516865 0.0
Predictions for 2022 issued by famed astrologer and doctor Nostradamus
https://t

1068 1473961112983019520 0.0
RT @DailyMail: Biden slams his own administration's response to COVID and lack of test kits https://t.co/XABrtZp8og

1069 1466313146918969348 0.0
Tom Udall, Biden’s cowboy boot-wearing friend, makes debut as ambassador to New Zealand https://t.co/OXxWlMVoGX

1070 1482122528864747521 0.0
Mum, 21, and seven-month-old baby go missing from their home https://t.co/Mk2h3leoWo https://t.co/vAQzwDueWV

1071 1499017933233668098 0.0
Italian Cream Cake  https://t.co/leqyy0GUxs #oldfashionedrecipes #recipes #Italian #cream #cake #homemade #scratch

1072 1485900947889045509 0.0
RT @DailyMailUK: Rishi Sunak issues thinly-veiled warning against dropping NI hike https://t.co/FepJgVqULv

1073 1484111488365256706 0.0
We've rounded up our favourite styles to try right now ranging from affordable to high-end ⬇️

 https://t.co/oLZZU7B7mm

1074 1466866218598555651 0.0
🗣️ "It’s time for MPs to turn off Twitter, put the phone down and start thinking critically"

"Otherwise, they m

...


20563 1485856727601922050 0.0
The reform led to an additional 7% of men and 9% of women staying in work, taking the male employment rate at age 65 to 42 per cent — the highest since the 1970s https://t.co/rdFPSwuU62

20564 1495233659875606530 0.0
Heart-stopping moment helicopter plunges into ocean off Miami beach filled with swimmers
https://t.co/wCyQG8b1AG

20565 1471125317595111430 0.0
@clarebalding will present Sports Personality of the Year (#SPOTY) on Sunday

@EmmaRaducanu is the favourite but Balding points out a strong shortlist of contenders including Tokyo Olympic champions @TomDaley1994 &amp; @adam_peaty 

Read the full interview 👇
https://t.co/ElTkPuWxkc

20566 1469307388708757509 0.0
Zegler reveals that Spielberg offered her advice one morning in the film’s Brooklyn studio.

“He took me by the shoulders and said, ‘Are you scared?’ And I said, ‘I am absolutely scared.’ And he said, ‘That’s good. You should use that!’”

20567 1474426283580923904 0.0
A pre-Christmas getaway t

20991 1497315465495912450 0.0
Brazen thief casually walks out of Tesco with a 50-inch TV https://t.co/FiUzpNuwqo

20992 1486673624903954432 0.0
The Fed policy error that should worry investors https://t.co/j1YVXatKOC

20993 1483382283188977664 0.0
RT @DailyMail: Michael Phelps says controversy surrounding trans UPenn swimmer Lia Thomas is 'very complicated' https://t.co/3M3dZxMRKk

20994 1472133803300827140 0.0
RT @expressceleb: Strictly’s Johannes says bond with 'traditionalist' mum has improved since John pairing #Strictly2021
https://t.co/2SzUvQ…

20995 1468162992395202562 0.0
#EastEnders history to be made with first polyamorous relationship for beloved residents? 

https://t.co/jMtDAKsiAK

20996 1473992045555507209 0.0
RT @mirrormorehope: Couple who struggled to get pregnant welcome baby boy after 13 years of trying https://t.co/2iPctbSFgu https://t.co/gT1…

20997 1496079319633907720 0.0
@bbcstrictly
 star @kuzmin__nikita
 posts sweet pictures with dance partner @tillyramsay https

21425 1487387548494315525 0.0
'Not perfect' #Strictly star Janette Manrara gives insight into marriage with Aljaz Skorjanec
https://t.co/ti3ILnBhAz https://t.co/e2ssdmMqQA

21426 1491021031573655553 0.0
Tom Brady REFUSES to rule out an NFL return despite the quarterback's decision to retire 
https://t.co/4j8IUlVgcN

21427 1468188087217967109 0.0
Dr Shola slams Prince Harry critics as she defends Duke's mental health appeal
https://t.co/3RUhNBOVOl

21428 1481861102166233089 0.0
Kanye 'Ye' West shares bizarre Instagram post after he's accused of punching fan in face outside of LA club
 https://t.co/0V4ufkV4S4

21429 1477995874131267588 0.0
Ministers confident new Covid restrictions are not needed https://t.co/DVfP9WfEFn

21430 1489428726949548033 0.0
Lidl sells kitchen gadget that shoppers say is the best £30 they’ve spent https://t.co/1tetQ4pPJ9

21431 1476493537437007874 0.0
Palace insiders have revealed that the royal family will never let Prince Andrew return to public life after Eps

21778 1471676748022661125 0.0
Which queso dip should you snag for your next cookout? We ranked them all. https://t.co/Q6BHCYbmuJ

21779 1497886408794591232 0.0
'It can feel like the vegetarian option has been pushed off the menu. If you don’t want meat, it’s go vegan or go home'  https://t.co/kim8KjOuj1

21780 1497980352786309122 0.0
Free to read: Historian Mary Elise Sarotte tells the inside story of how Vladimir Putin seized on the west's missteps while trying to secure a post-cold-war settlement https://t.co/cD9cMvmQml

21781 1489577802793988103 0.0
RT @MirrorFashion: Superdrug is having a huge fragrance sale in time for Valentine's Day https://t.co/tORJUaOiCA #affiliate https://t.co/iS…

21782 1468547952071294981 0.0
Huge Christmas tree set alight outside News Corps HQ as man arrested
https://t.co/MlpKaZPwoc https://t.co/QMFrE6Wmbt

21783 1484125676731043844 0.0
Tips to help with awful period pain including aromatherapy https://t.co/W9EKkoI3h4 #affiliate #periods #eco https://t.co/

The US stock market has suffered its worst start to the year since the global financial crisis, as the threat of rising interest rates, slowing corporate earnings growth and geopolitical tensions sent stocks tumbling across the board https://t.co/90skoy5qln

22232 1499353932224765952 0.0
Global commodity prices are on track for the biggest weekly rally in more than 50 years https://t.co/ePZ6Toi3jl https://t.co/wqlxmnhUUf

22233 1471055278296678407 0.0
Covid horror as more than a million face spending Christmas Day in isolation
https://t.co/1CKqMMerxJ https://t.co/OgrB9rrjTT

22234 1469381734059986948 0.0
When it comes to dealing with leftover bacon grease, here's what to do: https://t.co/WIJNWrbfmm

22235 1466763217942765568 0.0
Germany’s Covid wave could reach ‘sad peak’ at Christmas, outgoing minister says https://t.co/DORkzHTQcN

22236 1496091678553395206 0.0
"At 4am on February 22nd you'll feel our new policy," warned Vladimir Zhirinovsky on December 27 https://t.co/Cgmi8iehvU

222

## Global methods
Do not use releance feedback but global external sources

### Wordnet

In [ ]:
from nltk.corpus import wordnet as wn

In [ ]:
syns = wn.synsets('football', pos=wn.NOUN)
for syn in syns:
    lemmas = syn.lemmas()
    print(syn.definition())
    print(syn.examples())
    for lemma in lemmas:
        print(lemma.name())

### Wikidata
Check also [ConceptNet](https://conceptnet.io/)

In [ ]:
import requests

In [ ]:
endpoint = 'https://query.wikidata.org/sparql'

In [ ]:
sparql = """
select ?lexemeId ?lemma WHERE {
  ?lexemeId dct:language wd:Q1860;
            wikibase:lemma ?lemma.
  FILTER (regex(?lemma, '^pandemic.*'))
}
"""

In [ ]:
r = requests.get(endpoint, params={'query' : sparql}, 
                 headers={'Accept' : 'application/sparql-results+json'})
data = r.json()
statements = data['results']['bindings']

In [ ]:
statements

## Local methods
Exploits relevance feedback in order to learn new terminology

### Specificity score
$$
\delta(w) = p(w) \log \frac{p(w)}{q(w)}
$$

In [ ]:
import nltk
from collections import defaultdict

In [ ]:
def ngram(tokens):
    ng = list(nltk.ngrams(tokens, n=2))
    skip = []
    for i, (a, b) in enumerate(ng):
        skip.append((a, b))
        if i < len(ng) - 1:
            skip.append((a, ng[i+1][1]))
    return skip

In [ ]:
tweets = list(db.find())

In [ ]:
G = defaultdict(lambda: 0)
D = defaultdict(lambda: defaultdict(lambda: 0))
E = defaultdict(lambda: defaultdict(lambda: 0))

for tweet in tqdm(tweets):
    try:
        text = tweet['text']
        annotations = tweet['context_annotations']
        tokens = tokenize(text)
        ngr = ngram(tokens)
        for token in tokens:
            G[token] += 1
            for annotation in annotations:
                domain_name = annotation['domain']['name']
                D[domain_name][token] += 1
                entity_name = annotation['entity']['name']
                E[entity_name][token] += 1
        for (a, b) in ngr:
            bgram_key = "{}_{}".format(a, b)
            G[bgram_key] += 1
            for annotation in annotations:
                domain_name = annotation['domain']['name']
                D[domain_name][bgram_key] += 1
                entity_name = annotation['entity']['name']
                E[entity_name][bgram_key] += 1
    except KeyError:
        pass


In [ ]:
dstats.head(20)

In [ ]:
entity = 'Joe Biden'
domain = 'Sport'

In [ ]:
Etot = sum(E[entity].values())
Dtot = sum(D[domain].values())
Gtot = sum(G.values())
terms = {}
for word, count in D[domain].items():
    p_w = count / Dtot
    q_w = G[word] / Gtot
    terms[word] = p_w * np.log(p_w / q_w)

In [ ]:
R = pd.Series(terms)

In [ ]:
R.sort_values(ascending=False).head(20)

### Rocchio